# MovingPandas2

In [1]:
import pandas as pd 
import geopandas as gpd 
import movingpandas as mpd 
import shapely as shp 
import hvplot.pandas
import folium
import matplotlib.pyplot as plt

In [21]:
from geopandas import GeoDataFrame, read_file
from shapely.geometry import Point, LineString, Polygon
from datetime import datetime, timedelta
from holoviews import opts, dim

import warnings
warnings.filterwarnings('ignore')

plot_defaults = dict(linewidth=5, capstyle='round', figsize=(9,5))
opts.defaults(opts.Overlay(active_tools=['wheel_zoom']))
hvplot_defaults = {
    "tiles": "CartoLight",
    "frame_height": 320,
    "frame_width": 320,
    "cmap": "Viridis",
    "colorbar": True,
}

In [3]:
gdf = read_file('../data/demodata_geolife.gpkg')
gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 5908 entries, 0 to 5907
Data columns (total 6 columns):
 #   Column         Non-Null Count  Dtype   
---  ------         --------------  -----   
 0   id             5908 non-null   int64   
 1   sequence       5908 non-null   int64   
 2   trajectory_id  5908 non-null   int64   
 3   tracker        5908 non-null   int32   
 4   t              5908 non-null   object  
 5   geometry       5908 non-null   geometry
dtypes: geometry(1), int32(1), int64(3), object(1)
memory usage: 254.0+ KB


In [5]:
tc = mpd.TrajectoryCollection(gdf, 'trajectory_id', t='t')

In [6]:
tc.hvplot(line_width=7.0, tiles='CartoLight')

:Overlay
   .WMTS.I     :WMTS   [Longitude,Latitude]
   .Path.I     :Path   [Longitude,Latitude]
   .Path.II    :Path   [Longitude,Latitude]
   .Path.III   :Path   [Longitude,Latitude]
   .Path.IV    :Path   [Longitude,Latitude]
   .Path.V     :Path   [Longitude,Latitude]
   .Points.I   :Points   [Longitude,Latitude]   (triangle_angle)
   .Points.II  :Points   [Longitude,Latitude]   (triangle_angle)
   .Points.III :Points   [Longitude,Latitude]   (triangle_angle)
   .Points.IV  :Points   [Longitude,Latitude]   (triangle_angle)
   .Points.V   :Points   [Longitude,Latitude]   (triangle_angle)

In [7]:
tc.explore(column='trajectory_id', cmap='plasma', style_kwds=dict(weight=4))

## TrajectoryCollectionAggregator

Generalize the trajectories to speed calulcations

In [8]:
generalized = mpd.MinDistanceGeneralizer(tc).generalize(tolerance=100)

In [9]:
aggregator = mpd.TrajectoryCollectionAggregator(
    generalized, 
    max_distance=1000, 
    min_distance=100, 
    min_stop_duration=timedelta(minutes=5)
)

In [10]:
pts = aggregator.get_significant_points_gdf()
clusters = aggregator.get_clusters_gdf()
(pts.hvplot(geo=True, tiles='CartoLight')* clusters.hvplot(geo=True, color='red'))

:Overlay
   .WMTS.I    :WMTS   [Longitude,Latitude]
   .Points.I  :Points   [Longitude,Latitude]
   .Points.II :Points   [Longitude,Latitude]

In [11]:
m = pts.explore(marker_kwds={"radius": 3}, name="Significant points")

clusters.explore(m=m, color="red", marker_kwds={"radius": 3}, name="Cluster centroids")

folium.TileLayer("CartoDB positron").add_to(m)
folium.LayerControl().add_to(m)

m

In [14]:
flows = aggregator.get_flows_gdf() 
(
    flows.hvplot(
        geo=True, 
        hover_cols=['weight'], 
        line_width = dim('weight') * 7, 
        color='#1f77b3', 
        tiles='CartoLight'
    )
    * clusters.hvplot(geo=True, color='red', size=dim('n'))
)

:Overlay
   .WMTS.I   :WMTS   [Longitude,Latitude]
   .Path.I   :Path   [Longitude,Latitude]   (weight)
   .Points.I :Points   [Longitude,Latitude]   (n)

In [15]:
m = flows.explore(
    style_kwds={"weight": 5},
    name="Flows",
)

clusters.explore(
    m=m,
    color="red",
    style_kwds={"style_function": lambda x: {"radius": x["properties"]["n"]}},
    name="Clusters",
)

folium.TileLayer("OpenStreetMap").add_to(m)
folium.LayerControl().add_to(m)

m

# Smoothing trajectories

In [16]:
split = mpd.ObservationGapSplitter(tc).split(gap=timedelta(minutes=15))

## KasmanSmootherCV

This smoother operates on the assumption of a nearly-constant velocity (CV) model. The process_noise_std and measurement_noise_std parameters can be used to tune the smoother:

- `process_noise_std` governs the uncertainty associated with the adherence of the new (smooth) trajectories to the CV model assumption; higher values relax the assumption, therefore leading to less-smooth trajectories, and vice-versa.
- `measurement_noise_std` controls the assumed error in the original trajectories; higher values dictate that the original trajectories are expected to be noisier (and therefore, less reliable), thus leading to smoother trajectories, and vice-versa.

In [17]:
smooth = mpd.KalmanSmootherCV(split).smooth(
    process_noise_std=0.1, measurement_noise_std=10
)
print(smooth)

TrajectoryCollection with 11 trajectories


In [22]:
kwargs = {**hvplot_defaults, "line_width": 4}
(
    split.hvplot(title="Original Trajectories", **kwargs)
    + smooth.hvplot(title="Smooth Trajectories", **kwargs)
)

:Layout
   .Overlay.I  :Overlay
      .WMTS.I      :WMTS   [Longitude,Latitude]
      .Path.I      :Path   [Longitude,Latitude]
      .Path.II     :Path   [Longitude,Latitude]
      .Path.III    :Path   [Longitude,Latitude]
      .Path.IV     :Path   [Longitude,Latitude]
      .Path.V      :Path   [Longitude,Latitude]
      .Path.VI     :Path   [Longitude,Latitude]
      .Path.VII    :Path   [Longitude,Latitude]
      .Path.VIII   :Path   [Longitude,Latitude]
      .Path.IX     :Path   [Longitude,Latitude]
      .Path.X      :Path   [Longitude,Latitude]
      .Path.XI     :Path   [Longitude,Latitude]
      .Points.I    :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.II   :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.III  :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.IV   :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.V    :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.VI   :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.VII  :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.VIII :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.IX   :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.X    :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.XI   :Points   [Longitude,Latitude]   (triangle_angle)
   .Overlay.II :Overlay
      .WMTS.I      :WMTS   [Longitude,Latitude]
      .Path.I      :Path   [Longitude,Latitude]
      .Path.II     :Path   [Longitude,Latitude]
      .Path.III    :Path   [Longitude,Latitude]
      .Path.IV     :Path   [Longitude,Latitude]
      .Path.V      :Path   [Longitude,Latitude]
      .Path.VI     :Path   [Longitude,Latitude]
      .Path.VII    :Path   [Longitude,Latitude]
      .Path.VIII   :Path   [Longitude,Latitude]
      .Path.IX     :Path   [Longitude,Latitude]
      .Path.X      :Path   [Longitude,Latitude]
      .Path.XI     :Path   [Longitude,Latitude]
      .Points.I    :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.II   :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.III  :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.IV   :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.V    :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.VI   :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.VII  :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.VIII :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.IX   :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.X    :Points   [Longitude,Latitude]   (triangle_angle)
      .Points.XI   :Points   [Longitude,Latitude]   (triangle_angle)

In [23]:
kwargs = {**hvplot_defaults, "c": "speed", "line_width": 7, "clim": (0, 20)}
smooth.add_speed()
(
    split.trajectories[2].hvplot(title="Original Trajectory", **kwargs)
    + smooth.trajectories[2].hvplot(title="Smooth Trajectory", **kwargs)
)

:Layout
   .Overlay.I  :Overlay
      .WMTS.I   :WMTS   [Longitude,Latitude]
      .Path.I   :Path   [Longitude,Latitude]   (speed)
      .Points.I :Points   [Longitude,Latitude]   (speed,triangle_angle)
   .Overlay.II :Overlay
      .WMTS.I   :WMTS   [Longitude,Latitude]
      .Path.I   :Path   [Longitude,Latitude]   (speed)
      .Points.I :Points   [Longitude,Latitude]   (speed,triangle_angle)

# OutlierCleaner

In [24]:
traj = split.trajectories[8]
cleaned = traj.copy()
cleaned = mpd.OutlierCleaner(cleaned).clean(alpha=2)

smoothed = mpd.KalmanSmootherCV(cleaned).smooth(
    process_noise_std=0.1, measurement_noise_std=10
)

In [26]:
(
    traj.hvplot(title='Original Trajectory', **kwargs)
    + cleaned.hvplot(title='Cleaned Trajectory', **kwargs)
    + smoothed.hvplot(title='Cleaned and Smoothed', **kwargs)
)

:Layout
   .Overlay.I   :Overlay
      .WMTS.I   :WMTS   [Longitude,Latitude]
      .Path.I   :Path   [Longitude,Latitude]   (speed)
      .Points.I :Points   [Longitude,Latitude]   (speed,triangle_angle)
   .Overlay.II  :Overlay
      .WMTS.I   :WMTS   [Longitude,Latitude]
      .Path.I   :Path   [Longitude,Latitude]   (speed)
      .Points.I :Points   [Longitude,Latitude]   (speed,triangle_angle)
   .Overlay.III :Overlay
      .WMTS.I   :WMTS   [Longitude,Latitude]
      .Path.I   :Path   [Longitude,Latitude]   (speed)
      .Points.I :Points   [Longitude,Latitude]   (speed,triangle_angle)

# Measuring Distances